In [1]:
__author__ = 'Sanjay Seetharam'
__ID__ = '20031200'
__email__ = 'sanjay2.seetharam@live.uwe.ac.uk'
_Objective__ = ''' Analysis based on Aleksandra's plan
'''
__version__ = '7.6.2021'



In [2]:
# import and install libraries if missing
import sys
import subprocess
import pkg_resources

required = {'psycopg2','plotly','scikit-learn'}
installed = {pkg.key for pkg in pkg_resources.working_set}
missing = required - installed

if missing:
    python = sys.executable
    subprocess.check_call([python, '-m', 'pip', 'install', *missing], stdout=subprocess.DEVNULL)



In [3]:
import os # Handling file access
import numpy as np # Handling Numbers
import scipy as sp # Handling Numbers
import pandas as pd # Data Manipulation and Analysis
import psycopg2 # Database Manipulation
from psycopg2 import Error # Database Connection Issue Exception
import bamboolib as bam # GUI for transformations and visualisations
from pprint import pprint # Pretty print
from sklearn.preprocessing import OrdinalEncoder,OneHotEncoder, MinMaxScaler
import plotly.express as px # Data visualization
import configparser # Configuration Data for Database

In [4]:
def connect_database(username,password,database):
    '''
    purpose: Function to establish connection to database and return an connection object
    input: username, password
    output: Database connection status, connection object
    '''
    try:
        
        # Connect to an gapsquare database
        connection = psycopg2.connect(user=username,
                                      password=password,
                                      host="127.0.0.1",
                                      port="5432",
                                      database=database)

        # Create a cursor to perform database operations
        cursor = connection.cursor()
        
        # PostgreSQL details
        pprint("Database server information")
        print(connection.get_dsn_parameters(), "\n")
        
        # Executing a SQL query to fetch version info
        cursor.execute("SELECT version();")
        
        # Fetch result
        record = cursor.fetchone()
        print("You are connected to - ", record, "\n")
        
        return cursor
    
    except (Exception, Error) as error:
        pprint("Error while connecting to Database", error)
        

In [5]:
def import_data(fileName):
    '''
    purpose: Importing CSV file to DataFrame
    input: CSV file
    output: DataFrame
    '''
    inputDataFrame = pd.read_csv(fileName, sep=",", low_memory=False)
    return inputDataFrame

In [6]:
def fetch_data():
    '''
    purpose: Import Data
    output: Dataframe
    '''
    
    try:
        
        # Fetch Config data for database connection
        config = configparser.ConfigParser()
        config.read('app.ini')
        db_params = config['DB']
        
        # Establish connection with Database
        cur = connect_database(db_params['user'],db_params['password'], db_params['db'])
        
        # Executing query to all data from 'client_ethnic_extra' table
        data = cur.execute("SELECT * from client_ethnic_extra")
        
        # Fetching column names from DB
        colnames = [desc[0] for desc in cur.description]
        data = cur.fetchall()
        
        # Converting database result into dataframe
        inputData = pd.DataFrame(data,columns = colnames)     
        
        # Close Database connection
        if cur:
            cur.close()
            pprint("Database connection is closed")
        return inputData
    
    
    except Exception:
        inputFile = "idp_cleaned_data/cleaned_clientExtra.csv"
        inputData = import_data(inputFile)
        return inputData
    

#     finally:
#         if cur:
#             cur.close()
#             pprint("Database connection is closed")
     
        

In [7]:
# import data - CSV data to Dataframe
input_data = fetch_data()

'Database server information'
{'user': 'user_admin', 'dbname': 'gapsquare', 'host': '127.0.0.1', 'port': '5432', 'tty': '', 'options': '', 'sslmode': 'prefer', 'sslcompression': '0', 'gssencmode': 'prefer', 'krbsrvname': 'postgres', 'target_session_attrs': 'any'} 

You are connected to -  ('PostgreSQL 12.5 on x86_64-pc-linux-gnu, compiled by gcc (GCC) 4.8.3 20140911 (Red Hat 4.8.3-9), 64-bit',) 

'Database connection is closed'


In [8]:
# Check the shape of data
input_data.shape

(9382, 42)

In [9]:
def preprocess_data(data):
    '''
    purpose: Preprocessing of data (drop null,columns,standardize,categorize and group)
    input: dataframe - raw data
    output: dataframe - preprocessed data
    '''
    # Check details about data
    pprint(data.info())
    pprint(data.dtypes)
    
    
    # Dropping unnecessary columns
    data = data.drop(columns=['employee', 'rank_band','length_of_service'])
    
    # Converting non-numeric values to Uppercase
    data[list(data.select_dtypes(include = ['object']).columns)] = data[list(data.select_dtypes(include = ['object']).columns)].apply(lambda x: x.astype(str).str.upper())
    
    # Converting columns to category type
    data[['gender','disability','ft_pt','ethnicity']] = data[['gender','disability','ft_pt','ethnicity']].apply(lambda x : x.astype('category'))
    
    # Creating new columns for category with codes
    ord_enc = OrdinalEncoder()
    for col in ['gender','disability','ft_pt','ethnicity']:
        data[col+'_cat_temp'] = ord_enc.fit_transform(data[[col]])
    
    # Grouping Age Column
    data['age_cat_temp'] = pd.to_numeric(data['age'])
    bins = [18, 35, 50, 70]
    labels = ['18 to 35','35 to 50', '50 to 70']
    data['age_cat_temp'] = pd.cut(data['age_cat_temp'], bins, labels = labels)

    # Convert Salary per month column datatype to numeric
    data['salary_per_month'] = pd.to_numeric(data['salary_per_month'])
    
    return data
    

In [10]:
preprocessed_data = preprocess_data(input_data)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9382 entries, 0 to 9381
Data columns (total 42 columns):
 #   Column                       Non-Null Count  Dtype 
---  ------                       --------------  ----- 
 0   employee                     9382 non-null   int64 
 1   main_band_range              9382 non-null   object
 2   rank_band                    9382 non-null   object
 3   pay_point                    9382 non-null   object
 4   monthly_pay_basic            9382 non-null   object
 5   gender                       9382 non-null   object
 6   disability                   9382 non-null   object
 7   age                          9382 non-null   object
 8   actual_worked_hours          9382 non-null   object
 9   full_time_equivalent         9382 non-null   object
 10  ft_pt                        9382 non-null   object
 11  service_start_date           9382 non-null   object
 12  length_of_service            9382 non-null   object
 13  ethnicity                    9382

In [11]:
''' Salary average for each feature
    1. Consider features based on PCA result (salary band, age groups and length of service)
    2. Group by each feature with its mean and create a series 
    3. Create a dict of avg val each feature and avg val monthly salary
    4. Create new columns with those values for each feature
'''
for each_feature in ('main_band_range','age_cat_temp','service_start_date'):
    
    average_val = preprocessed_data.groupby(each_feature, as_index=False)['salary_per_month'].mean() 

    average_val_dict = pd.Series(average_val.salary_per_month.values, index=average_val[each_feature]).to_dict()
    
    preprocessed_data.insert(loc=preprocessed_data.columns.get_loc(each_feature) + 1, column='norm_salary_%s' % each_feature,
                            value=[np.nan for i in range(preprocessed_data.shape[0])])
    
    preprocessed_data["norm_salary_%s" % each_feature] = preprocessed_data[each_feature].apply(lambda x: average_val_dict.get(x))
    

print(preprocessed_data.shape)
preprocessed_data.head()
    

(9382, 47)


main_band_range  norm_salary_main_band_range pay_point monthly_pay_basic  \
0          BAND D                  2959.388479       4.0           2578.33   
1             BB3                  8284.813333       0.0           8142.75   
2          BAND A                  6944.788086       4.0           5855.83   
3          BAND D                  2959.388479       4.0           2578.33   
4          BAND E                  2366.189620       4.0           1879.85   

   gender disability   age actual_worked_hours full_time_equivalent ft_pt  \
0  FEMALE    UNKNOWN  39.0                36.0                  1.0    FT   
1    MALE    UNKNOWN  50.0                36.0                  1.0    FT   
2    MALE    UNKNOWN  50.0                36.0                  1.0    FT   
3  FEMALE    UNKNOWN  44.0                36.0                  1.0    FT   
4  FEMALE         NO  28.0                30.0                 0.83    PT   

   ... hourly_pay  salary_per_week salary_per_month salary_annual_35_ft  \
0  ...      17.91           626.68          2715.60            32587.23   
1  ...      56.55          1979.14          8576.28           102915.31   
2  ...      40.67          1423.29          6167.60            74011.18   
3  ...      17.91           626.68          2715.60            32587.23   
4  ...      15.67           548.29          2375.92            28511.06   

  gender_cat_temp disability_cat_temp ft_pt_cat_temp ethnicity_cat_temp  \
0             0.0                 2.0            0.0                0.0   
1             1.0                 2.0            0.0                1.0   
2             1.0                 2.0            0.0                1.0   
3             0.0                 2.0            0.0                1.0   
4             0.0                 0.0            1.0                0.0   

  age_cat_temp norm_salary_age_cat_temp  
0     35 to 50              2926.131324  
1     35 to 50              2926.131324  
2     35 to 50              2926.131324  
3     35 to 50              2926.131324  
4     18 to 35              2552.705802  

[5 rows x 47 columns]

In [12]:
norm_values = []

# Add every normalised column values to a list
for each_col in preprocessed_data.columns:
    if each_col[:4] == 'norm':
        norm_values.append(each_col)
        
# Find mean of normalised values        
average_salary = preprocessed_data[norm_values].mean(axis=1)

# Create new column normalised_salary from the previous value
preprocessed_data.insert(loc = preprocessed_data.columns.get_loc('salary_per_month') + 1, column='normalised_salary', value=average_salary)

# Find difference of actual and normalised salary 
raw_difference = preprocessed_data['salary_per_month'] - preprocessed_data['normalised_salary']

# Create new column raw_salary_difference from the previous value
preprocessed_data.insert(loc = preprocessed_data.columns.get_loc('normalised_salary') + 1, column='raw_salary_difference', value=raw_difference)

# Create a -1 to 1 distributions scaler obj
scaler = MinMaxScaler(feature_range=(-1,1))

# Transform data to shape according to scaler - Standard Deviation
SD = scaler.fit_transform(preprocessed_data.raw_salary_difference.values.reshape(-1,1))

# Create new column SD from the previous value 
preprocessed_data.insert(loc = preprocessed_data.columns.get_loc('raw_salary_difference') + 1, column='SD', value=SD.flatten())

'''
# Find the absolute minimum salary difference value
min_sal_val = min(preprocessed_data.raw_salary_difference, key=abs)

for value in preprocessed_data.raw_salary_difference:
    if value == min_sal_val:
        print(value)
'''

# print(preprocessed_data.index[preprocessed_data['raw_salary_difference'] == value].tolist()) 

pay_label = []
numeric_pay_label = []

# Create new column with pay labels based on the standard deviation
for value in preprocessed_data.SD:
    if value < -0.6:
        pay_label.append('underpaid')
        numeric_pay_label.append(-1)
    elif value > -0.45:
        pay_label.append('overpaid')
        numeric_pay_label.append(1)
    else:
        pay_label.append('fairly_paid')
        numeric_pay_label.append(0)
        
preprocessed_data.insert(loc = preprocessed_data.columns.get_loc('raw_salary_difference') + 2, column = 'pay_label', value = pay_label)

preprocessed_data.insert(loc = preprocessed_data.columns.get_loc('raw_salary_difference') + 3, column = 'numeric_pay_label', value = numeric_pay_label)

print(preprocessed_data.shape)
preprocessed_data.head()


(9382, 52)


main_band_range  norm_salary_main_band_range pay_point monthly_pay_basic  \
0          BAND D                  2959.388479       4.0           2578.33   
1             BB3                  8284.813333       0.0           8142.75   
2          BAND A                  6944.788086       4.0           5855.83   
3          BAND D                  2959.388479       4.0           2578.33   
4          BAND E                  2366.189620       4.0           1879.85   

   gender disability   age actual_worked_hours full_time_equivalent ft_pt  \
0  FEMALE    UNKNOWN  39.0                36.0                  1.0    FT   
1    MALE    UNKNOWN  50.0                36.0                  1.0    FT   
2    MALE    UNKNOWN  50.0                36.0                  1.0    FT   
3  FEMALE    UNKNOWN  44.0                36.0                  1.0    FT   
4  FEMALE         NO  28.0                30.0                 0.83    PT   

   ...        SD  pay_label numeric_pay_label salary_annual_35_ft  \
0  ... -0.786668  underpaid                -1            32587.23   
1  ... -0.088128   overpaid                 1           102915.31   
2  ... -0.444575   overpaid                 1            74011.18   
3  ... -0.784534  underpaid                -1            32587.23   
4  ... -0.791056  underpaid                -1            28511.06   

  gender_cat_temp disability_cat_temp ft_pt_cat_temp ethnicity_cat_temp  \
0             0.0                 2.0            0.0                0.0   
1             1.0                 2.0            0.0                1.0   
2             1.0                 2.0            0.0                1.0   
3             0.0                 2.0            0.0                1.0   
4             0.0                 0.0            1.0                0.0   

  age_cat_temp norm_salary_age_cat_temp  
0     35 to 50              2926.131324  
1     35 to 50              2926.131324  
2     35 to 50              2926.131324  
3     35 to 50              2926.131324  
4     18 to 35              2552.705802  

[5 rows x 52 columns]

In [13]:
# Create an output folder if not exists
if not os.path.exists("output"):
    os.mkdir("output")

In [ ]:
''' Following visualisations can be optimised (rather an generalised approach) but lazy '''

In [21]:
# Distribution of payscale by gender
try:
    fig = px.violin(preprocessed_data.dropna(subset=['age_cat_temp']), x='gender', y='SD', color='gender', color_discrete_sequence=px.colors.qualitative.Alphabet, box=True, title='Distribution of payscale by gender')
    fig.update_xaxes(title_text='Gender')
    fig.update_yaxes(title_text='Pay Scale')
    fig.update_layout(legend_title_text='Gender')
    fig.write_image("output/analysis1.png")
    fig.show()
except Exception as e1:
    print("Exception analysis1: ",str(e1))
    

In [22]:
# Distribution of male and female payscale ordered by age groups
try:
    fig = px.violin(preprocessed_data.dropna(subset=['age_cat_temp']), x='age_cat_temp', y='SD', color='gender', color_discrete_sequence=px.colors.qualitative.Alphabet, box=True, title="Distribution of male and female payscale ordered by age groups")
    fig.update_xaxes(title_text='Age Group')
    fig.update_yaxes(title_text='Pay Scale')
    fig.update_layout(legend_title_text='Gender')
    fig.write_image("output/analysis2.png")  
    fig.show()
except Exception as e1:
    print("Exception analysis2: ",str(e1))    


In [23]:
# # Distribution of male and female payscale ordered by age group and classified by Ethnicity 
try:
    fig = px.violin(preprocessed_data.dropna(subset=['age_cat_temp']), x='age_cat_temp', y='SD', facet_col='ethnicity', color='gender', color_discrete_sequence=px.colors.qualitative.Alphabet,labels={'ethnicity': 'Ethnicity'}, box=True, title="Distribution of male and female payscale ordered by age group and classified by Ethnicity ")
    fig.update_layout(legend_title_text='Gender')
    fig.update_xaxes(title_text='Age Group')
    fig.update_yaxes(title_text='Pay Scale')
    fig.write_image("output/analysis3.png")  
    fig.show()
except Exception as e1:
    print("Exception analysis3: ",str(e1))

In [24]:
# Distribution of Male and Female Salary ordered by age group and classified by Ethnicity and Job Type
try:
    fig = px.violin(preprocessed_data.dropna(subset=['age_cat_temp']), x='age_cat_temp', y='SD', facet_col='ethnicity', color='gender', color_discrete_sequence=px.colors.qualitative.Alphabet, facet_row='ft_pt', width=1100, height=1101, labels={'ft_pt': 'Job Type', 'ethnicity': 'Ethnicity'}, box=True, title="Distribution of Male and Female Salary ordered by Pay Status and classified by Ethnicity and Job Type ")
    fig.update_layout(legend_title_text='Gender')
    fig.update_xaxes(title_text='Age Group')
    fig.update_yaxes(title_text='Pay Scale')
    fig.write_image("output/analysis4.png")  
    fig.show()
except Exception as e1:
    print("Exception analysis4: ",str(e1))

In [25]:
# Distribution of male and female payscale ordered by pay status and classified by Ethnicity 
try:
    fig = px.violin(preprocessed_data.dropna(subset=['pay_label']), x='pay_label', y='salary_per_month', facet_col='ethnicity', color='gender', color_discrete_sequence=px.colors.qualitative.Alphabet,labels={'ethnicity': 'Ethnicity'}, box=True, title="Distribution of male and female payscale ordered by age group and classified by Ethnicity ")
    fig.update_xaxes(title_text='Pay Status')
    fig.update_yaxes(title_text='Monthy Salary')
    fig.update_layout(legend_title_text='Gender')
    fig.write_image("output/analysis5.png")  
    fig.show()
except Exception as e1:
    print("Exception analysis5: ",str(e1))        


In [26]:
# Distribution of Male and Female Salary ordered by Pay Status and classified by Ethnicity and Job Type
try:
    fig = px.violin(preprocessed_data.dropna(subset=['pay_label']), x='pay_label', y='salary_per_month', facet_col='ethnicity', color='gender', color_discrete_sequence=px.colors.qualitative.Alphabet, facet_row='ft_pt', width=1100, height=1101, labels={'ft_pt': 'Job Type', 'ethnicity': 'Ethnicity'}, box=True, title="Distribution of Male and Female Salary ordered by Pay Status and classified by Ethnicity and Job Type ")
    fig.update_layout(legend_title_text='Gender')
    fig.update_xaxes(title_text='Pay Status')
    fig.update_yaxes(title_text='Salary')
    fig.write_image("output/analysis6.png")  
    fig.show()
except Exception as e1:
    print("Exception analysis6: ",str(e1))    